In [1]:
## import system installed packages.
import os                # for filesystem access
import sys               # for system sensors on flowing tensors.
import tensorflow as tf  # lets the tensors flow.
import numpy as np       # most tf objects are built from numpy.
import pandas as pd      # data holder manager.
from pandas.io.json import json_normalize  # json to pandas converter.
from datetime import datetime, timedelta   # need unix 2 real and visa-versa.
import time                 # i never know which time is better for what... but there is no time for that...
import json                 # data from web comes as json.
import urllib               # for web calls.
from urllib import request  # for secure web connections.
import random
from collections import deque

In [2]:
## we are gonna try to NOT use anything that isnt pypy installable or on
## this page... This page is going to get long i think. from this point,
## setting up ALL the global variables, like fs_paths, save points, how
## much work to do, web urls if necessary, global stuff.

In [3]:
class Options(object):
    """An object that contains all global variables that might be needed,
       in various locations.
       
       A good way to put the human readable controls upfront where the
       driver can find them.
    """

    def __init__(self):
        """All public options go here."""
        self.model_save_path = 'save_path'  # NOT SET
        self.data_save_path = 'data_path'   # NOT SET
        self.data_filename = 'poloniex_historical_data_all_{}.npz'
        
        #### poloniex api variables #####
        self._coin = 'BTC_DGB'
        self._candle_period = 300
        # about 2 weeks ... now - a million seconds
        self._start_time = int(time.time()) - 1000000
        # 9999999999 means most current by poloniex standard api
        # see how im mixing time libs cause i dont know whats better?
        self._end_time = int(time.time())

    def __str__(self):
        """Make sense from calling an object, not a memory position."""
        return self.model_save_path

    def __call__(self):
        """Directly print out all available options."""
        print("##########\n#\tAll Available Options:")
        for i in sorted(self.__dict__):
            print("#\t{}:  {}".format(i, self.__dict__['{}'.format(i)]))
### The options CLASS is refered to as the CONFIG(config)...
config = Options()

In [4]:
### Print out all the config usage and variables.
while False:
    print("Config itself is reference to the model save path:\n\t{}".format(
        config))
    print("Calling config will print a list of all the options for reference.")
    config()
    break;

In [5]:
### No Api credentials are necessary, poloniex would like to see,
### less than 20 api calls a minute... so sleep for 3 secs is best,
### BUT... i think you can get 20 a sec at most... but I wouldnt push it.
def quote_history(coin="BTC_ETH", period=900, start=00, end=9999999999):
    """Poloniex public chart data with candlesticks."""
    # start = int(time.time() - 1000000)
    with urllib.request.urlopen(
        'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'.format(
        coin, start, end, period
        )
                    ) as url:
        data = json.loads(url.read().decode('UTF-8'))
    return data

def ticker():
    """Poloniex public ticker."""
    with urllib.request.urlopen(
        'https://poloniex.com/public?command=returnTicker'
                    ) as url:
        data = json.loads(url.read().decode('UTF-8'))
    return data

while False:
    # test to make sure we are getting the api call right.
    print(quote_history(config._coin, 
                        config._candle_period, 
                        config._start_time+99000,
                        config._end_time))
    print(ticker())
    break;

In [6]:
### poloniex reports everything in unix time. But plotting in real-time
### is better. So we need to convert back and forth.

In [7]:
def to_unix_time(dt):
    """Take a datetime formated string and return a unix time."""
    epoch =  datetime.utcfromtimestamp(0)
    return (dt - epoch).total_seconds() * 1000
def to_date_time(ut):
    """You guessed it! take a unix time string.
       THEN handle with care(float,int), then return just the date.
    """
    return datetime.fromtimestamp(int(float(ut))).strftime('%Y-%m-%d')

In [8]:
### GENERALLY using of a pandas dataframe accessing the Yahoo stock api
### is what is used in most tutorials. Now that our poloniex apicall is 
### real similiar to the yahoo one. we should be able to use this data in
### real-time.

In [9]:
# Collect a test dataframe from the exchange
df = json_normalize(quote_history(config._coin,
                                  config._candle_period,
                                  config._start_time,
                                  config._end_time))

In [10]:
# print(df)
for i in df:
    print(i)

close
date
high
low
open
quoteVolume
volume
weightedAverage


In [11]:
per_day = 0
for p, d in zip(df['close'], df['date']):
    d = to_date_time(d)
    if '26' in d:
        per_day += 1
    # print("{0}: {1:.8f}".format(d, float(p)))
print("# of quotes per day", per_day)
print("# of quotes in dataset", len(df))

# of quotes per day 184
# of quotes in dataset 3334


In [12]:
stock_data = df
day_len = per_day

In [13]:
my_train = np.zeros((len(stock_data)-day_len, day_len), dtype=np.float)
my_train

array([[ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       ..., 
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.]])

In [14]:
for i in range(0, len(my_train)):
    for j in range(0, day_len):
        my_train[i,j] = float(stock_data['close'][i+j])
        #my_train[i,j] = data_rsi[i+j]
print(my_train)

[[  2.98000000e-06   2.98000000e-06   2.98000000e-06 ...,   2.99000000e-06
    2.97000000e-06   2.97000000e-06]
 [  2.98000000e-06   2.98000000e-06   2.99000000e-06 ...,   2.97000000e-06
    2.97000000e-06   2.96000000e-06]
 [  2.98000000e-06   2.99000000e-06   2.99000000e-06 ...,   2.97000000e-06
    2.96000000e-06   2.99000000e-06]
 ..., 
 [  4.34000000e-06   4.31000000e-06   4.32000000e-06 ...,   4.12000000e-06
    4.11000000e-06   4.11000000e-06]
 [  4.31000000e-06   4.32000000e-06   4.30000000e-06 ...,   4.11000000e-06
    4.11000000e-06   4.13000000e-06]
 [  4.32000000e-06   4.30000000e-06   4.29000000e-06 ...,   4.11000000e-06
    4.13000000e-06   4.12000000e-06]]


In [ ]:
class TWStock():
    def __init__(self, stock_data):
        print("Setting up TWStock")
        self.stock_data = stock_data
        self.stock_index = 0
    
    def render(self):
        return 
    
    def reset(self):
        self.stock_index = 0
        return self.stock_data[self.stock_index]
    
    def step(self, action): 
        self.stock_index += 1
        action_reward = self.stock_data[self.stock_index][day_len-1] - self.stock_data[self.stock_index][day_len-2] 
        if (action == 0):
            action_reward = 0
        if (action == 2):
            action_reward = -1 * action_reward

        stock_done = False
        if self.stock_index >= len(self.stock_data)-1:
            stock_done = True
        else:
            stock_done = False
        return self.stock_data[self.stock_index], action_reward, stock_done, 0

In [ ]:
# Hyper Parameters for DQN
GAMMA = 0.9 # discount factor for target Q
INITIAL_EPSILON = 0.5 # starting value of epsilon
FINAL_EPSILON = 0.01 # final value of epsilon
REPLAY_SIZE = 10000 # experience replay buffer size
BATCH_SIZE = 32 # size of minibatch

class DQN():
    # DQN Agent
    def __init__(self, env):
        # init experience replay
        self.replay_buffer = deque()

        # init some parameters
        self.time_step = 0
        self.epsilon = INITIAL_EPSILON

        #self.state_dim = env.observation_space.shape[0]
        #self.action_dim = env.action_space.n

        self.state_dim = day_len
        self.action_dim = 3


        self.create_Q_network()
        self.create_training_method()

        # Init session
        self.session = tf.InteractiveSession()
        self.session.run(tf.initialize_all_variables())

    def create_Q_network(self):
        # network weights
        W1 = self.weight_variable([self.state_dim, 20])
        b1 = self.bias_variable([20])
        W2 = self.weight_variable([20, self.action_dim])
        b2 = self.bias_variable([self.action_dim])
        # input layer
        self.state_input = tf.placeholder("float",[None,self.state_dim])
        # hidden layers
        h_layer = tf.nn.relu(tf.matmul(self.state_input,W1) + b1)
        # Q Value layer
        self.Q_value = tf.matmul(h_layer,W2) + b2

    def create_training_method(self):
        self.action_input = tf.placeholder("float",[None,self.action_dim])
        # one hot presentation
        self.y_input = tf.placeholder("float",[None])
        Q_action = tf.reduce_sum(tf.multiply(self.Q_value,self.action_input),reduction_indices = 1)
        self.cost = tf.reduce_mean(tf.square(self.y_input - Q_action))
        self.optimizer = tf.train.AdamOptimizer(0.0001).minimize(self.cost)
        # self.optimizer = tf.train.RMSPropOptimizer(0.01,0.1).minimize(self.cost)

    def perceive(self,state,action,reward,next_state,done):
        one_hot_action = np.zeros(self.action_dim)
        one_hot_action[action] = 1
        self.replay_buffer.append((state,one_hot_action,reward,next_state,done))

        if len(self.replay_buffer) > REPLAY_SIZE:
          self.replay_buffer.popleft()

        if len(self.replay_buffer) > BATCH_SIZE:
          self.train_Q_network()

    def train_Q_network(self):
        self.time_step += 1

        # Step 1: obtain random minibatch from replay memory
        minibatch = random.sample(self.replay_buffer,BATCH_SIZE)
        state_batch = [data[0] for data in minibatch]
        action_batch = [data[1] for data in minibatch]
        reward_batch = [data[2] for data in minibatch]
        next_state_batch = [data[3] for data in minibatch]

        # Step 2: calculate y
        y_batch = []
        Q_value_batch = self.Q_value.eval(feed_dict={self.state_input:next_state_batch})

        for i in range(0,BATCH_SIZE):
            done = minibatch[i][4]
            if done:
                y_batch.append(reward_batch[i])
            else :
                y_batch.append(reward_batch[i] + GAMMA * np.max(Q_value_batch[i]))

        self.optimizer.run(feed_dict={
          self.y_input:y_batch,
          self.action_input:action_batch,
          self.state_input:state_batch
          })


    def egreedy_action(self,state):
        Q_value = self.Q_value.eval(feed_dict = {
          self.state_input:[state]})[0]
        if random.random() <= self.epsilon:
          return random.randint(0,self.action_dim - 1)
        else:
          return np.argmax(Q_value)

        self.epsilon -= (INITIAL_EPSILON - FINAL_EPSILON)/10000


    def action(self,state):
        return np.argmax(self.Q_value.eval(feed_dict = {self.state_input:[state]})[0])


    def weight_variable(self,shape):
        initial = tf.truncated_normal(shape)
        return tf.Variable(initial)

    def bias_variable(self,shape):
        initial = tf.constant(0.01, shape = shape)
        return tf.Variable(initial)

# ---------------------------------------------------------
 # Hyper Parameters
ENV_NAME = 'TF_polo'
EPISODE = 50000 # Episode limitation
STEP = 1000     #300 # Step limitation in an episode
TEST = 10       # The number of experiment test every 100 episode


def main():
    print("|###| Starting program")

    # initialize OpenAI Gym env and dqn agent
    #env = gym.make(ENV_NAME)
    env = TWStock(my_train) 
    agent = DQN(env)

    for episode in range(EPISODE):
        print("|###|Episode: {} of {} |###|".format(episode, EPISODE))
        # initialize task
        state = env.reset()
        # print("|###| State: ", state)
        # Train
        for step in range(STEP):
            print("|###| Step: {} of {} |###|".format(step, STEP))
            action = agent.egreedy_action(state) # e-greedy action for trai
            print("|###| Taking Action: ", action)
            next_state, reward, done,_ = env.step(action)
            print("|###| Reward for action: {0:.8f}".format(reward))
            # print("|###| Next State: ", next_state)
            # Define reward for agent ??? WTF
            reward_agent = -1 if done else 0.1
            print("|###| Reward agent:", reward_agent)
            agent.perceive(state, action, reward, next_state, done)
            state = next_state
            if done:
                print("|###| We are now Done")
                break

        # Test every 100 episodes
        if episode % 100 == 0:
            print("|###| Beginning testing phase.")
            total_reward = 0

            for i in range(TEST):
                state = env.reset()

            for j in range(STEP):
                env.render()
                action = agent.action(state)   # direct action for test
                state,reward,done,_ = env.step(action)
                total_reward += reward
                if done:
                    break

            ave_reward = total_reward/TEST
            print('|###| episode: {} | '.format(episode),
                'Evaluation Average Reward: {:.12f}'.format(float(ave_reward)))

            if ave_reward >= 200:
                print("End of Program")
                break


if __name__ == '__main__':
    main()

|###| Starting program
Setting up TWStock
Instructions for updating:
Use `tf.global_variables_initializer` instead.
|###|Episode: 0 of 50000 |###|
|###| Step: 0 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 1 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000003
|###| Reward agent: 0.1
|###| Step: 2 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 3 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 4 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 5 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 6 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 7 of 1000 |###|
|###| Taking Action:  2
|###| Reward 

|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 73 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 74 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000002
|###| Reward agent: 0.1
|###| Step: 75 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 76 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 77 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 78 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 79 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 80 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Ste

|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 203 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 204 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 205 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 206 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 207 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 208 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 209 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000002
|###| Reward agent: 0.1
|###| Step: 210 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 211 of 1000 |#

|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 329 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 330 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 331 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 332 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 333 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000002
|###| Reward agent: 0.1
|###| Step: 334 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000003
|###| Reward agent: 0.1
|###| Step: 335 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 336 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 337 of 1000

|###| Reward agent: 0.1
|###| Step: 453 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 454 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 455 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 456 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 457 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000006
|###| Reward agent: 0.1
|###| Step: 458 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 459 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000003
|###| Reward agent: 0.1
|###| Step: 460 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000003
|###| Reward agent: 0.1
|###| Step: 461 of 1000 |###|
|###| Taking Action:  0
|###| Rew

...

|###| Reward agent: 0.1
|###| Step: 25 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 26 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 27 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 28 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 29 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 30 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 31 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000002
|###| Reward agent: 0.1
|###| Step: 32 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 33 of 1000 |###|
|###| Taking Action:  0
|###| Reward for 

|###| Step: 215 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 216 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 217 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 218 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000003
|###| Reward agent: 0.1
|###| Step: 219 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 220 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 221 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 222 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 223 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00

|###| Step: 405 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 406 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000004
|###| Reward agent: 0.1
|###| Step: 407 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 408 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000002
|###| Reward agent: 0.1
|###| Step: 409 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 410 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 411 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000002
|###| Reward agent: 0.1
|###| Step: 412 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 413 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000

|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 596 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 597 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000000
|###| Reward agent: 0.1
|###| Step: 598 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 599 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 600 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 601 of 1000 |###|
|###| Taking Action:  2
|###| Reward for action: -0.00000002
|###| Reward agent: 0.1
|###| Step: 602 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 603 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000003
|###| Reward agent: 0.1


|###| Reward agent: 0.1
|###| Step: 781 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 782 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: -0.00000001
|###| Reward agent: 0.1
|###| Step: 783 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 784 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 785 of 1000 |###|
|###| Taking Action:  1
|###| Reward for action: 0.00000001
|###| Reward agent: 0.1
|###| Step: 786 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 787 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 788 of 1000 |###|
|###| Taking Action:  0
|###| Reward for action: 0.00000000
|###| Reward agent: 0.1
|###| Step: 789 of 1000 |###|
|###| Taking Action:  0
|###| Rew